In [1]:
import pandas as pd
import numpy as np
import os
import pystan

In [2]:
df = pd.read_csv('/Users/albert/git/RTLib/Alignments/FP18_20180801_1/ev_converted.txt', sep='\t')
df

sequence         raw_file  retention_time  \
0                 _AAAAAAALQAK_  180413S_X_FP18H          33.308   
1                 _AAAAAAALQAK_  180413S_X_FP18I          33.216   
2                 _AAAAAAALQAK_  180413S_X_FP18I          33.223   
3                 _AAAAAAALQAK_  180413S_X_FP18J          32.911   
4                 _AAAAAAALQAK_  180413S_X_FP18J          32.917   
5                 _AAAAAAALQAK_  180413S_X_FP18K          32.974   
6                 _AAAAAAALQAK_  180413S_X_FP18K          32.967   
7                      _AAAAAK_  180413S_X_FP18F          21.060   
8                      _AAAAAK_  180413S_X_FP18G          21.088   
9                      _AAAAAK_  180413S_X_FP18I          21.064   
10                     _AAAAAK_  180413S_X_FP18J          20.830   
11                     _AAAAAK_  180413S_X_FP18K          20.620   
12                    _AAATPAK_  180413S_X_FP18A          20.212   
13                    _AAATPAK_  180413S_X_FP18B          18.422   
14                    _AAATPAK_  180413S_X_FP18B          20.334   
15                    _AAATPAK_  180413S_X_FP18C          20.279   
16                    _AAATPAK_  180413S_X_FP18D          20.192   
17                    _AAATPAK_  180413S_X_FP18E          20.171   
18                    _AAATPAK_  180413S_X_FP18F          20.176   
19                    _AAATPAK_  180413S_X_FP18G          20.190   
20                    _AAATPAK_  180413S_X_FP18H          20.254   
21                    _AAATPAK_  180413S_X_FP18I          20.197   
22                    _AAATPAK_  180413S_X_FP18J          19.950   
23                    _AAATPAK_  180413S_X_FP18K          17.996   
24                    _AAATPAK_  180413S_X_FP18K          19.814   
25                   _AAATPAKK_  180413S_X_FP18D          20.809   
26                   _AAATPAKK_  180413S_X_FP18E          20.814   
27                   _AAATPAKK_  180413S_X_FP18F          20.815   
28                   _AAATPAKK_  180413S_X_FP18G          20.831   
29                   _AAATPAKK_  180413S_X_FP18H          20.877   
...                         ...              ...             ...   
13780  _YTPSGQAGAAASESLFVSNHAY_  180413S_X_FP18B          41.348   
13781  _YTPSGQAGAAASESLFVSNHAY_  180413S_X_FP18C          41.278   
13782  _YTPSGQAGAAASESLFVSNHAY_  180413S_X_FP18D          41.211   
13783  _YTPSGQAGAAASESLFVSNHAY_  180413S_X_FP18E          41.216   
13784  _YTPSGQAGAAASESLFVSNHAY_  180413S_X_FP18F          41.150   
13785  _YTPSGQAGAAASESLFVSNHAY_  180413S_X_FP18G          41.175   
13786  _YTPSGQAGAAASESLFVSNHAY_  180413S_X_FP18H          41.327   
13787  _YTPSGQAGAAASESLFVSNHAY_  180413S_X_FP18I          41.266   
13788  _YTPSGQAGAAASESLFVSNHAY_  180413S_X_FP18J          40.907   
13789  _YTPSGQAGAAASESLFVSNHAY_  180413S_X_FP18K          41.089   
13790               _YYDYSGAFR_  180413S_X_FP18A          16.564   
13791               _YYDYSGAFR_  180413S_X_FP18B          16.643   
13792               _YYDYSGAFR_  180413S_X_FP18G          16.444   
13793              _YYGGGSEGGR_  180413S_X_FP18A          17.865   
13794              _YYGGGSEGGR_  180413S_X_FP18B          17.872   
13795              _YYGGGSEGGR_  180413S_X_FP18D          17.639   
13796              _YYGGGSEGGR_  180413S_X_FP18E          17.557   
13797              _YYGGGSEGGR_  180413S_X_FP18G          17.451   
13798              _YYGGGSEGGR_  180413S_X_FP18I          17.510   
13799              _YYGGGSEGGR_  180413S_X_FP18J          17.531   
13800              _YYGGGSEGGR_  180413S_X_FP18K          17.452   
13801                  _YYLAPK_  180413S_X_FP18A          34.805   
13802                  _YYLAPK_  180413S_X_FP18B          35.269   
13803                  _YYLAPK_  180413S_X_FP18C          35.332   
13804                  _YYLAPK_  180413S_X_FP18E          35.187   
13805                  _YYLAPK_  180413S_X_FP18G          35.128   
13806                  _YYLAPK_  180413S_X_FP18H          35.208   
13807      

In [3]:
dff = df[~df['exclude']].reset_index(drop=True)

In [4]:
dff['stan_peptide_id'] = dff['sequence'].map({
ind: val for val, ind in enumerate(dff['sequence'].unique())})

exp_names = np.sort(dff['raw_file'].unique())
num_experiments = len(exp_names)
num_observations = dff.shape[0]
num_peptides = dff['stan_peptide_id'].max() + 1

# build a unique peptide-experiment ID
pep_exp_all = dff['stan_peptide_id'].map(str) + ' - ' + dff['exp_id'].map(str)
pep_exp_pairs = pep_exp_all.unique()
num_pep_exp_pairs = len(pep_exp_pairs)

# muij_map - maps pair ID back to dataframe index
muij_map = pep_exp_all.map({ind: val for val, ind in enumerate(pep_exp_pairs)})
# maps to experiment and peptide ID
splt = pd.Series(pep_exp_pairs).str.split(' - ')
muij_to_pep = splt.str.get(0).map(int)
muij_to_exp = splt.str.get(1).map(int)

In [5]:
# build dictionary of data to feed to STAN
# revert all data to primitive types to avoid problems later
# STAN code is all 1-indexed, so add 1 to all indexed forms of data
stan_data = {
    'num_experiments': num_experiments,
    'num_peptides': num_peptides,
    'num_pep_exp_pairs': num_pep_exp_pairs,
    'num_total_observations': num_observations,
    'muij_map': muij_map+1,
    'muij_to_pep': (muij_to_pep+1).tolist(),
    'muij_to_exp': (muij_to_exp+1).tolist(),
    'experiment_id': (dff['exp_id']+1).tolist(),
    'peptide_id': (dff['stan_peptide_id']+1).tolist(),
    'retention_times': dff['retention_time'].tolist(),
    'mean_log_rt': np.mean(np.log(dff['retention_time'])),
    'sd_log_rt': np.std(np.log(dff['retention_time'])),
    'rt_mean': np.mean(dff['retention_time']),
    'rt_std': np.std(dff['retention_time']),
    'pep': dff['pep'].tolist(),
    'max_retention_time': dff['retention_time'].max()
}

In [6]:
pep_threshold = 0.5
rt_distortion = 0.1
mu_min = 1

# get the average retention time for a peptide, weighting by PEP
def get_mu(x):
    weights = ((1 - x['pep'].values) - (1 - pep_threshold)) / pep_threshold
    return np.sum(x['retention_time'].values * weights) / np.sum(weights)

# apply the get_mu function on all peptides and add some distortion
mu_init = dff.groupby('stan_peptide_id')[['pep', 'retention_time']].apply(get_mu).values \
    + np.random.normal(0, rt_distortion, num_peptides)

# negative or very low retention times not allowed. floor at 5 minutes
mu_init[mu_init <= mu_min] = mu_min
# canonical retention time shouldn't be bigger than largest real RT
mu_max = dff['retention_time'].max()
mu_init[mu_init > mu_max] = mu_max

rt_distorted = dff['retention_time'] + np.random.normal(0, rt_distortion, num_observations)
# make sure distorted retention times stay within bounds of real ones
rt_distorted[rt_distorted > dff['retention_time'].max()] = dff['retention_time'].max()
rt_distorted[rt_distorted < dff['retention_time'].min()] = dff['retention_time'].min()

# initialize priors for the segmented linear regression
# first element of vector is beta_0, or the intercept
# second element is beta_1 and beta_2, the slopes of the two segments
beta_init = np.array((\
    np.repeat(10, num_experiments), \
    np.repeat(1, num_experiments)), dtype=float)

mu_pred = np.zeros(num_peptides)
# temporary data frame to quickly map over in the loop
dft = pd.DataFrame(dict(\
    stan_peptide_id=dff['stan_peptide_id'], 
    exp_id=dff['exp_id'], 
    pep=dff['pep'], 
    retention_time=mu_init[dff['stan_peptide_id']]))

prior_iters = 10

for i in range(0, prior_iters):
    # for each experiment, fit a simple linear regression
    # between the distorted RTs and the initial canonical retention times
    for j in range(0, num_experiments):
        idx     = (dff['exp_id'] == j)
        rt_cur  = rt_distorted[idx]
        mu_cur  = mu_init[dff['stan_peptide_id'][idx]]
        pep_cur = dff['pep'][idx]

        # for this experiment, run a linear regression (1 degree polyfit)
        # of the mus and the distorted RTs. store the linear regression params
        m, c = np.polyfit(mu_cur, rt_cur, 1, w=(1 - pep_cur))
        beta_init[(0,1), j] = [c, m]

    # calculate new set of canonical RTs based on linear regression params
    mu_pred = (rt_distorted - beta_init[0][dff['exp_id']]) / beta_init[1][dff['exp_id']] 
    # make sure new canonical RTs are within same range as distorted RTs
    mu_pred[mu_pred <= 0] = rt_distorted.min()
    mu_pred[mu_pred >= rt_distorted.max()] = rt_distorted.max()
    dft['retention_time'] = np.copy(mu_pred)

    mu_prev = np.copy(mu_init)

    # new set of priors for canonical RTs based on weighted combination of
    # this set of predicted canonical RTs
    mu_init = dft.groupby('stan_peptide_id')[['pep', 'retention_time']].apply(get_mu).values

    print('Iter {} | Avg. canonical RT shift: {:.5f}'.format(i + 1, 
      pow(np.sum(mu_prev - mu_init), 2) / len(mu_init)))
mu_init

Iter 1 | Avg. canonical RT shift: 0.22529
Iter 2 | Avg. canonical RT shift: 0.01242
Iter 3 | Avg. canonical RT shift: 0.00128
Iter 4 | Avg. canonical RT shift: 0.00040
Iter 5 | Avg. canonical RT shift: 0.00027
Iter 6 | Avg. canonical RT shift: 0.00025
Iter 7 | Avg. canonical RT shift: 0.00024
Iter 8 | Avg. canonical RT shift: 0.00024
Iter 9 | Avg. canonical RT shift: 0.00024
Iter 10 | Avg. canonical RT shift: 0.00024


array([33.13809228, 21.03617424, 20.11172858, ..., 16.25176082,
       17.54158513, 35.09573606])

In [7]:
# grab linear regression params
beta_0 = beta_init[0]
beta_1 = beta_init[1]

# apply lower bound of (-1.0 * min(beta_1) * min(muInit)) to beta_0
# where (-1.0 * min(beta_1) * min(muInit)) is the lowest possible intercept
# given the lowest possible mu and lowest possible beta_1
beta_0[beta_0 <= (-1 * beta_1.min() * mu_init.min())] = \
(-1 * beta_1.min() * mu_init.min()) + 1e-3
# apply lower bound of 0 to beta_1
beta_1[beta_1 <= 0] = 1e-3

# apply upper bound to prior canonical RTs
mu_init[mu_init >= dff['retention_time'].max()] = 0.95 * dff['retention_time'].max()

# create prior list for STAN
init_list = {
    'mu': mu_init,
    #'sigma': sigma_init,
    'beta_0': beta_0,
    'beta_1': beta_1,
    'sigma_slope': np.repeat(0.1, num_experiments),
    'sigma_intercept': np.repeat(0.1, num_experiments)
}
# set beta_2 (slope of second segment) to the same as the slope of the 1st segment
beta_2 = np.copy(init_list['beta_1'])
# apply lower bound of 0 to beta_2
beta_2[beta_2 <= 0] = 1e-3

# set beta_2
init_list['beta_2'] = beta_2
# set split point to be the median canonical RT
init_list['split_point'] = np.repeat(np.median(init_list['mu']), 
                                   len(init_list['beta_0']))
init_list

{'beta_0': array([ 0.98044038,  0.3045449 ,  0.32453715,  0.19975537,  0.11529832,
         0.0803374 ,  0.15616099,  0.19093283,  0.00883332, -0.08632538,
        -0.7865462 ]),
 'beta_1': array([0.96433541, 0.99707806, 0.9958996 , 0.99644353, 0.99877332,
        0.99637459, 0.99629361, 0.99856007, 1.00169972, 0.99558431,
        1.02007857]),
 'beta_2': array([0.96433541, 0.99707806, 0.9958996 , 0.99644353, 0.99877332,
        0.99637459, 0.99629361, 0.99856007, 1.00169972, 0.99558431,
        1.02007857]),
 'mu': array([33.13809228, 21.03617424, 20.11172858, ..., 16.25176082,
        17.54158513, 35.09573606]),
 'sigma_intercept': array([0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1]),
 'sigma_slope': array([0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1]),
 'split_point': array([32.54595835, 32.54595835, 32.54595835, 32.54595835, 32.54595835,
        32.54595835, 32.54595835, 32.54595835, 32.54595835, 32.54595835,
        32.54595835])}

In [8]:
with open('/Users/albert/git/RTLib/dart_id/models/fit_RT3e.stan', 'r') as f:
    model_code = f.read()

sm = pystan.StanModel(model_name='FitRTE', model_code=model_code)
sm

INFO:pystan:COMPILING THE C++ CODE FOR MODEL FitRTE_ce2c2e2ee0e47f3ca31ecb5ad931c73b NOW.


In [38]:
op = sm.optimizing(data=stan_data, init=init_list, iter=3000, verbose=True, save_iterations=True)
op

/Users/albert/anaconda3/lib/python3.6/site-packages/pystan/misc.py:399: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  elif np.issubdtype(np.asarray(v).dtype, float):


OrderedDict([('mu',
              array([33.10378946, 21.02462151, 20.13623666, ..., 16.4642407 ,
                     17.6135402 , 34.99830091])),
             ('beta_1',
              array([0.99213428, 1.00612123, 1.00720809, 1.00473941, 1.00903885,
                     1.0042618 , 1.01091351, 1.00787395, 1.01211165, 0.99901851,
                     0.9990376 ])),
             ('beta_2',
              array([0.94970695, 0.9915691 , 0.98470504, 0.99103527, 0.99097805,
                     0.9950275 , 0.99137012, 0.99223339, 0.99739587, 0.99009217,
                     1.02039289])),
             ('beta_0',
              array([ 0.29140782,  0.06728977,  0.02249064, -0.0183011 , -0.14831801,
                     -0.10986209, -0.20018515, -0.05385805, -0.21545453, -0.15717035,
                     -0.28243596])),
             ('split_point',
              array([30.69780461, 34.52786547, 35.8948702 , 34.44250116, 34.16917676,
                     31.32399922, 29.98303279, 34.2963998 , 

In [43]:
op['mu_pred']

#op['mu'][dff['stan_peptide_id']]
#np.mean(op['muij'][muij_map] - dff['retention_time'])
#np.mean(op['mu'][dff['stan_peptide_id']] - op['mu_pred'][muij_map])


array([33.08946637, 33.11766896, 33.0716467 , ..., 34.94387505,
       35.04552295, 35.12219008])

In [25]:
fit = pystan.stan(file='/Users/albert/git/RTLib/dart_id/models/fit_RT3e.stan', model_name='FitRTE', 
                  data=stan_data, 
                  init=[init_list], iter=100, warmup=50, chains=1, verbose=True)
fit

INFO:pystan:COMPILING THE C++ CODE FOR MODEL FitRTE_ce2c2e2ee0e47f3ca31ecb5ad931c73b NOW.
INFO:pystan:OS: darwin, Python: 3.6.4 |Anaconda custom (64-bit)| (default, Jan 16 2018, 12:04:33) 
[GCC 4.2.1 Compatible Clang 4.0.1 (tags/RELEASE_401/final)], Cython 0.27.3


Compiling /var/folders/t7/l57lffj15m36y4j19v66lz2c0000gn/T/tmpwhlogdrt/stanfit4FitRTE_ce2c2e2ee0e47f3ca31ecb5ad931c73b_5574459205108210578.pyx because it changed.
[1/1] Cythonizing /var/folders/t7/l57lffj15m36y4j19v66lz2c0000gn/T/tmpwhlogdrt/stanfit4FitRTE_ce2c2e2ee0e47f3ca31ecb5ad931c73b_5574459205108210578.pyx
building 'stanfit4FitRTE_ce2c2e2ee0e47f3ca31ecb5ad931c73b_5574459205108210578' extension
creating /var/folders/t7/l57lffj15m36y4j19v66lz2c0000gn/T/tmpwhlogdrt/var
creating /var/folders/t7/l57lffj15m36y4j19v66lz2c0000gn/T/tmpwhlogdrt/var/folders
creating /var/folders/t7/l57lffj15m36y4j19v66lz2c0000gn/T/tmpwhlogdrt/var/folders/t7
creating /var/folders/t7/l57lffj15m36y4j19v66lz2c0000gn/T/tmpwhlogdrt/var/folders/t7/l57lffj15m36y4j19v66lz2c0000gn
creating /var/folders/t7/l57lffj15m36y4j19v66lz2c0000gn/T/tmpwhlogdrt/var/folders/t7/l57lffj15m36y4j19v66lz2c0000gn/T
creating /var/folders/t7/l57lffj15m36y4j19v66lz2c0000gn/T/tmpwhlogdrt/var/folders/t7/l57lffj15m36y4j19v66lz2c0000gn/T/tmpw

/Users/albert/anaconda3/lib/python3.6/site-packages/pystan/misc.py:399: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  elif np.issubdtype(np.asarray(v).dtype, float):


Inference for Stan model: FitRTE_ce2c2e2ee0e47f3ca31ecb5ad931c73b.
1 chains, each with iter=100; warmup=50; thin=1; 
post-warmup draws per chain=50, total post-warmup draws=50.

                      mean se_mean     sd   2.5%    25%    50%    75%  97.5%  n_eff   Rhat
mu[0]                 33.1  3.8e-3   0.03  33.04  33.08   33.1  33.11  33.16     47   0.98
mu[1]                21.02  3.9e-3   0.03  20.97   21.0  21.02  21.04  21.07     42   0.98
mu[2]                20.12  3.2e-3   0.01  20.09  20.11  20.12  20.13  20.15     18    1.0
mu[3]                20.73  3.7e-3   0.03  20.69  20.71  20.73  20.75  20.79     50    1.0
mu[4]                28.27  5.2e-3   0.03  28.21  28.25  28.27   28.3  28.32     41   1.04
mu[5]                28.49  4.4e-3   0.03  28.45  28.47  28.49  28.51  28.56     40   1.02
mu[6]                22.22  3.7e-3   0.02  22.18  22.21  22.22  22.23  22.25     22   0.99
mu[7]                23.31  2.9e-3   0.02  23.27   23.3  23.31  23.32  23.37     50   0.98
mu[

In [ ]:
sample1 = sm.sampling(data=stan_data, pars=['mu', 'mu_pred'], init=[op], chains=1, iter=100, verbose=True)
sample1

In [170]:
from scipy.stats import norm, laplace, bernoulli, binom

In [64]:
laplace.rvs(loc=0, scale=1, size=100).reshape(5, 20)
b = np.array([[1,2,3], [4,5,6], [7,8,9]])
print(np.apply_along_axis(np.mean, 0, b))
print(b)

[4. 5. 6.]
[[1 2 3]
 [4 5 6]
 [7 8 9]]


In [65]:
myfunc = np.median
myfunc([1, 2, 3])

2.0

In [69]:
def weighted_median(values, weights):
  order = np.argsort(values)
  values = values[order]
  weights = weights[order]

  #weighted_quantiles = (np.cumsum(weights) - (0.5 * weights)) / np.sum(weights)
  
  return np.interp(0.5, 
    (np.cumsum(weights) - (0.5 * weights)) / np.sum(weights),
    values)

weighted_median(np.array([0, 1, 4, 5, 5]), np.array([1, 2, 1, 8, 1]))

4.666666666666667

In [111]:
laplace.rvs(size=20).reshape(4, 5) * np.array([1, 10, 100, 1000, 10000])

array([[-2.11093406e-01, -2.95323046e+01,  2.77791805e+01,
         8.52757031e+02, -4.99632626e+03],
       [-2.04083975e+00,  6.30622400e-01, -3.11080622e+02,
        -2.38837193e+02, -1.47828834e+04],
       [-2.24056200e+00,  2.94337514e+01, -1.80349213e+02,
        -2.25211343e+03, -1.75609969e+04],
       [-2.99919375e+00, -2.71201784e+00, -2.30552437e+02,
         4.66379846e+02,  1.55535841e+04]])

In [174]:
bernoulli.rvs(0.5, size=100)
binom.rvs(100, [0.5, 0.25])

array([48, 23])

In [178]:
np.array([[0, 1], [2, 3]])[:,0]

array([0, 2])

In [180]:
rv = norm(loc=0, scale=10)
rv.rvs(10)

array([ -6.72857529,  -1.93620142, -13.09164977,  -4.43138259,
        15.37267444,  -1.19571807, -16.29474579,   9.07824218,
        -8.61839348,  12.13151481])

In [192]:
# generate frozen null distributions for each experiment
num_experiments = df['exp_id'].max() + 1
null_dists = df.groupby('exp_id')['retention_time'].agg([np.mean, np.std])
null_dists = [norm(loc=null_dists.loc[i, 'mean'], scale=null_dists.loc[i, 'std']) for i in range(0, num_experiments)]
null_dists[0].rvs(100)

array([43.63119923, 37.13290286, 22.7628955 , 31.14506899, 27.0207896 ,
       39.2534015 , 47.81128438, 27.277361  , 24.00538594, 29.57188441,
       30.49277924, 29.74274526, 40.15376399, 29.52610105, 32.91259632,
       46.67753422, 41.67186935, 32.65794247, 44.91313811, 34.97033399,
       52.9749177 , 43.84354391, 26.04023654, 19.29685815, 37.08764486,
       41.66906485, 38.97041038, 35.26957604, 40.49882981, 20.96416579,
       26.10815246, 32.80157228, 48.37259318, 34.15345164, 21.39731334,
       39.73399482, 24.56201281, 55.52791651, 10.47692003, 28.45417853,
       26.92427513, 24.03320483, 33.78558787, 19.69146355, 26.35261263,
       29.12676492, 21.37138155, 45.29078154, 28.55002576, 44.75289466,
       44.04660338, 19.56345009, 49.51402665, 26.09176931, 45.3576608 ,
       37.77410417, 28.29901465, 23.73180448, 25.96332937, 41.24353421,
       35.29851575, 22.36691932, 29.88380035, 25.40885412, 48.85023331,
       27.5134669 , 44.58143166, 23.37398316, 31.95671957, 29.18